In [2]:
"""IMPORT LIBRARIES"""

import numpy as np
import pandas as pd
import plotly.express as px

from utils import darcy_weisbach_pressure_drop, pump_pressure_rise, valve_pressure_drop, valve_cv

In [3]:
"""darcy_weisbach_pressure_drop"""

flowrates = np.linspace(0, 0.3, 100)
FRICTION_FACTOR = 0.02
PIPE_LENGTH = 10.0
pipe_diameters = np.logspace(1e-3, 0.5, 500)
DENSITY = 1000

flowrates, pipe_diameters = np.meshgrid(flowrates, pipe_diameters)
flowrates = flowrates.flatten()
pipe_diameters = pipe_diameters.flatten()

df = pd.DataFrame({
    'flowrate': flowrates,
    'friction_factor': FRICTION_FACTOR,
    'pipe_length': PIPE_LENGTH,
    'pipe_diameter': pipe_diameters,
    "density": DENSITY
})

df['pressure_drop'] = darcy_weisbach_pressure_drop(df['flowrate'], df['friction_factor'], df['pipe_length'], df['pipe_diameter'], df['density'])

fig = px.scatter_3d(df, x='flowrate', y='pipe_diameter', z='pressure_drop', color='pressure_drop')
fig.update_traces(marker=dict(size=3))
fig.update_layout(template='plotly_dark', paper_bgcolor='#1f1f1f')
fig.show()

In [4]:
"""pump_pressure_rise"""


flowrates = np.linspace(0, 0.12, 100)
pump_speeds = np.linspace(0.2, 1, 9)
DENSITY = 1000


flowrates, pump_speeds = np.meshgrid(flowrates, pump_speeds)
flowrates = flowrates.flatten()
pump_speeds = np.round(pump_speeds.flatten(), 2)

df = pd.DataFrame({
    'flowrate': flowrates,
    'pump_speed': pump_speeds,
    'density': DENSITY
})

df['pressure_rise'] = np.array([pump_pressure_rise(row['flowrate'], row['pump_speed'], row['density']) for index, row in df.iterrows()])


fig = px.line(df, x='flowrate', y='pressure_rise', color='pump_speed')
fig.update_traces(marker=dict(size=3))
fig.update_layout(template='plotly_dark', paper_bgcolor='#1f1f1f')

In [20]:
"""valve_pressure_drop"""

flowrates = np.linspace(0, 0.3, 100)
valve_positions = np.linspace(0, 1, 11)

flowrates, valve_positions = np.meshgrid(flowrates, valve_positions)
flowrates = flowrates.flatten()
valve_positions = np.round(valve_positions.flatten(), 2)

df = pd.DataFrame({
    'flowrate': flowrates,
    'valve_position': valve_positions,
    'valve_cv': valve_cv(valve_positions)
})

df['pressure_drop'] = np.array([valve_pressure_drop(row['flowrate'], row['valve_position']) for index, row in df.iterrows()])

fig = px.line(df[df["flowrate"]==flowrates[0]], x='valve_position', y='valve_cv')
fig.update_traces(marker=dict(size=3))
fig.update_layout(template="plotly_dark", paper_bgcolor="#1f1f1f")
fig.show()

fig = px.line(
    df[
        df["valve_position"] == valve_positions[-1]
    ],
    x="flowrate",
    y="pressure_drop",
    color="valve_position",
)
fig.update_traces(marker=dict(size=3))
fig.update_layout(template='plotly_dark', paper_bgcolor='#1f1f1f')